# Snap Roll Template Generation

This notebook compares a generated template snap roll to one recorded with a 2m F3A plane using Ardupilot.

In [1]:
from flightanalysis import Section, Line, Snap
from geometry import Transformation, Point
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from flightplotting.plots import plotsec
from flightplotting.traces import axis_rate_trace, control_input_trace, aoa_trace
import numpy as np
from geometry import Quaternion

nb_layout = dict(width=800, 
        height=300, 
        margin=dict(l=5, r=5, t=5, b=1), 
        legend=dict(yanchor="top", xanchor="left", x=0.8, y=0.99)
        )

The template snap is generated using the Section.from_snap constructor. Below short sections of line are also appended before and after the snap for easier comparison to the template section.

In [3]:

line_before = Line(2).create_template(Transformation(rotation=Quaternion.from_euler(Point(np.pi, 0, 0))), 30)

snap = Snap(1).scale(170).create_template(line_before[-1].transform, 30)

line_after = Line(2).create_template(snap[-1].transform, 30)

snap = Section.stack([line_before, snap,  line_after])


Some real snaps were recorded using Ardupilot and saved as a section csv. The sections are transformed so that the sections x axis points along the line the snap is on and the y axis is parallel to wings at the start of the section. This is done in the local_section function.

In [14]:
snap_sec = Section.from_csv("examples/snap_roll_section.csv")

from geometry import Transformation, Coord

def local_section(base_sec):
    first_state = base_sec.get_state_from_index(0)
    last_state = base_sec.get_state_from_index(-1)
    wing_axis = first_state.att.transform_point(Point(0,-1,0))
    snap_coord = Coord.from_xy(first_state.pos, last_state.pos - first_state.pos, wing_axis)

    transform = Transformation.from_coords(snap_coord, Coord.from_nothing())

    temp = base_sec.transform(transform)
    temp = temp.transform(Transformation(-temp.get_state_from_index(0).pos))
    temp.data.index = temp.data.index - temp.data.index[0]
    return temp

snap_sections = [
    local_section(snap_sec.subset(536,538)),
    local_section(snap_sec.subset(545.5,546.5)),
    local_section(snap_sec.subset(558.3,559.9)),
    local_section(snap_sec.subset(547.5,549.4)),
    local_section(snap_sec.subset(581.3,582.7)),
    
]


The figures below compare 3D visualisations of the constructed snap to one of the flown snaps

In [15]:

def plotsnap(sec):
    fig = plotsec(sec, nmodels=10, scale=2, show_axes = True, color="grey")
    fig.update_layout(width=1200, height=300, margin=dict(l=0, r=0, t=0, b=0))
    return fig

plotsnap(snap).show()
plotsnap(snap_sections[4]).show()

The graphs below show control inputs and axis rates for two of the flown snaps. 

In [16]:
from flightplotting.plots import control_brv_plot


control_brv_plot(snap_sections[4]).update_layout(width=800,height=300).show()

#plot_snap_controls(snap_sections[3]).show()

The graphs below compare axis rates, alpha and beta between one of the recorded snaps and the template.

In [19]:
from flightplotting.plots import aoa_brv_plot

aoa_brv_plot(snap_sections[4]).update_layout(width=800,height=300).show()
aoa_brv_plot(snap).update_layout(width=800,height=300).show()

In [20]:
from flightplotting.traces import sec_col_trace

def plot_snap_bvel(sec):   


    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_traces(axis_rate_trace(sec), secondary_ys=[False for i in range(3)])

#    fig.add_traces(aoa_trace(sec), secondary_ys=[True for i in range(2)])
    fig.add_traces(sec_col_trace(sec, sec.bvel.columns, dash="dash"), secondary_ys=np.full(3, True))

    fig.update_layout(
        xaxis=dict(title="time, s"),
        yaxis=dict(title="axis rate, rad/s"),
        yaxis2=dict(title="angle of attach, deg"),
        **nb_layout
    )

    return fig

plot_snap_bvel(snap_sections[4]).show()